In [ ]:
import numpy as np
import pickle

BOARD_ROWS = 3
BOARD_COLS = 3
BOARD_SIZE = BOARD_ROWS * BOARD_COLS

class State:
    def __init__(self):
        # the board is represented by an n * n array,
        # 1 represents a chessman of the player who moves first,
        # -1 represents a chessman of another player
        # 0 represents an empty position
        self.data = np.zeros((BOARD_ROWS, BOARD_COLS))
        self.winner = None
        self.hash_val = None
        self.end = None

    # compute the hash value for one state, it's unique
    def hash(self):
        if self.hash_val is None:
            self.hash_val = 0
            for i in self.data.reshape(BOARD_ROWS * BOARD_COLS):
                if i == -1:
                    i = 2
                self.hash_val = self.hash_val * 3 + i
        return int(self.hash_val)

    # check whether a player has won the game, or it's a tie
    def is_end(self):
        if self.end is not None:
            return self.end
        results = []
        # check row
        for i in range(0, BOARD_ROWS):
            results.append(np.sum(self.data[i, :]))
        # check columns
        for i in range(0, BOARD_COLS):
            results.append(np.sum(self.data[:, i]))

        # check diagonals
        results.append(0)
        for i in range(0, BOARD_ROWS):
            results[-1] += self.data[i, i]
        results.append(0)
        for i in range(0, BOARD_ROWS):
            results[-1] += self.data[i, BOARD_ROWS - 1 - i]

        for result in results:
            if result == 3:
                self.winner = 1
                self.end = True
                return self.end
            if result == -3:
                self.winner = -1
                self.end = True
                return self.end

        # whether it's a tie
        sum = np.sum(np.abs(self.data))
        if sum == BOARD_ROWS * BOARD_COLS:
            self.winner = 0
            self.end = True
            return self.end

        # game is still going on
        self.end = False
        return self.end

    # @symbol: 1 or -1
    # put chessman symbol in position (i, j)
    def next_state(self, i, j, symbol):
        new_state = State()
        new_state.data = np.copy(self.data)
        new_state.data[i, j] = symbol
        return new_state

    # print the board
    def print(self):
        for i in range(0, BOARD_ROWS):
            print('-------------')
            out = '| '
            for j in range(0, BOARD_COLS):
                if self.data[i, j] == 1:
                    token = '*'
                if self.data[i, j] == 0:
                    token = '0'
                if self.data[i, j] == -1:
                    token = 'x'
                out += token + ' | '
            print(out)
        print('-------------')

def get_all_states_impl(current_state, current_symbol, all_states):
    for i in range(0, BOARD_ROWS):
        for j in range(0, BOARD_COLS):
            if current_state.data[i][j] == 0:
                newState = current_state.next_state(i, j, current_symbol)
                newHash = newState.hash()
                if newHash not in all_states.keys():
                    isEnd = newState.is_end()
                    all_states[newHash] = (newState, isEnd)
                    if not isEnd:
                        get_all_states_impl(newState, -current_symbol, all_states)

def get_all_states():
    current_symbol = 1
    current_state = State()
    all_states = dict()
    all_states[current_state.hash()] = (current_state, current_state.is_end())
    get_all_states_impl(current_state, current_symbol, all_states)
    return all_states

# all possible board configurations
all_states = get_all_states()

class Judger:
    # @player1: the player who will move first, its chessman will be 1
    # @player2: another player with a chessman -1
    # @feedback: if True, both players will receive rewards when game is end
    def __init__(self, player1, player2):
        self.p1 = player1
        self.p2 = player2
        self.current_player = None
        self.p1_symbol = 1
        self.p2_symbol = -1
        self.p1.set_symbol(self.p1_symbol)
        self.p2.set_symbol(self.p2_symbol)
        self.current_state = State()

    def reset(self):
        self.p1.reset()
        self.p2.reset()

    def alternate(self):
        while True:
            yield self.p1
            yield self.p2

    # @print: if True, print each board during the game
    def play(self, print=False):
        alternator = self.alternate()
        self.reset()
        current_state = State()
        self.p1.set_state(current_state)
        self.p2.set_state(current_state)
        while True:
            player = next(alternator)
            if print:
                current_state.print()
            [i, j, symbol] = player.act()
            next_state_hash = current_state.next_state(i, j, symbol).hash()
            current_state, is_end = all_states[next_state_hash]
            self.p1.set_state(current_state)
            self.p2.set_state(current_state)
            if is_end:
                if print:
                    current_state.print()
                return current_state.winner

# AI player
class Player:
    # @step_size: the step size to update estimations
    # @epsilon: the probability to explore
    def __init__(self, step_size=0.1, epsilon=0.1):
        self.estimations = dict()
        self.step_size = step_size
        self.epsilon = epsilon
        self.states = []
        self.greedy = []

    def reset(self):
        self.states = []
        self.greedy = []

    def set_state(self, state):
        self.states.append(state)
        self.greedy.append(True)

    def set_symbol(self, symbol):
        self.symbol = symbol
        for hash_val in all_states.keys():
            (state, is_end) = all_states[hash_val]
            if is_end:
                if state.winner == self.symbol:
                    self.estimations[hash_val] = 1.0
                elif state.winner == 0:
                    # we need to distinguish between a tie and a lose
                    self.estimations[hash_val] = 0.5
                else:
                    self.estimations[hash_val] = 0
            else:
                self.estimations[hash_val] = 0.5

    # update value estimation
    def backup(self):
        # for debug
        # print('player trajectory')
        # for state in self.states:
        #     state.print()

        self.states = [state.hash() for state in self.states]

        for i in reversed(range(len(self.states) - 1)):
            state = self.states[i]
            td_error = self.greedy[i] * (self.estimations[self.states[i + 1]] - self.estimations[state])
            self.estimations[state] += self.step_size * td_error

    # choose an action based on the state
    def act(self):
        state = self.states[-1]
        next_states = []
        next_positions = []
        for i in range(BOARD_ROWS):
            for j in range(BOARD_COLS):
                if state.data[i, j] == 0:
                    next_positions.append([i, j])
                    next_states.append(state.next_state(i, j, self.symbol).hash())

        if np.random.rand() < self.epsilon:
            action = next_positions[np.random.randint(len(next_positions))]
            action.append(self.symbol)
            self.greedy[-1] = False
            return action

        values = []
        for hash, pos in zip(next_states, next_positions):
            values.append((self.estimations[hash], pos))
        np.random.shuffle(values)
        values.sort(key=lambda x: x[0], reverse=True)
        action = values[0][1]
        action.append(self.symbol)
        return action

    def save_policy(self):
        with open('policy_%s.bin' % ('first' if self.symbol == 1 else 'second'), 'wb') as f:
            pickle.dump(self.estimations, f)

    def load_policy(self):
        with open('policy_%s.bin' % ('first' if self.symbol == 1 else 'second'), 'rb') as f:
            self.estimations = pickle.load(f)

# human interface
# input a number to put a chessman
# | q | w | e |
# | a | s | d |
# | z | x | c |
class HumanPlayer:
    def __init__(self, **kwargs):
        self.symbol = None
        self.keys = ['q', 'w', 'e', 'a', 's', 'd', 'z', 'x', 'c']
        self.state = None
        return

    def reset(self):
        return

    def set_state(self, state):
        self.state = state

    def set_symbol(self, symbol):
        self.symbol = symbol
        return

    def backup(self, _):
        return

    def act(self):
        self.state.print()
        key = input("Input your position:")
        data = self.keys.index(key)
        i = data // int(BOARD_COLS)
        j = data % BOARD_COLS
        return (i, j, self.symbol)

def train(epochs):
    player1 = Player(epsilon=0.01)
    player2 = Player(epsilon=0.01)
    judger = Judger(player1, player2)
    player1_win = 0.0
    player2_win = 0.0
    for i in range(1, epochs + 1):
        winner = judger.play(print=False)
        if winner == 1:
            player1_win += 1
        if winner == -1:
            player2_win += 1
        print('Epoch %d, player 1 win %.02f, player 2 win %.02f' % (i, player1_win / i, player2_win / i))
        player1.backup()
        player2.backup()
        judger.reset()
    player1.save_policy()
    player2.save_policy()

def compete(turns):
    player1 = Player(epsilon=0)
    player2 = Player(epsilon=0)
    judger = Judger(player1, player2)
    player1.load_policy()
    player2.load_policy()
    player1_win = 0.0
    player2_win = 0.0
    for i in range(0, turns):
        winner = judger.play()
        if winner == 1:
            player1_win += 1
        if winner == -1:
            player2_win += 1
        judger.reset()
    print('%d turns, player 1 win %.02f, player 2 win %.02f' % (turns, player1_win / turns, player2_win / turns))

# The game is a zero sum game. If both players are playing with an optimal strategy, every game will end in a tie.
# So we test whether the AI can guarantee at least a tie if it goes second.
def play():
    while True:
        player1 = HumanPlayer()
        player2 = Player(epsilon=0)
        judger = Judger(player1, player2)
        player2.load_policy()
        winner = judger.play()
        if winner == player2.symbol:
            print("You lose!")
        elif winner == player1.symbol:
            print("You win!")
        else:
            print("It is a tie!")

if __name__ == '__main__':
    train(int(1e5))
    compete(int(1e3))
play()

Epoch 1, player 1 win 0.00, player 2 win 1.00
Epoch 2, player 1 win 0.50, player 2 win 0.50
Epoch 3, player 1 win 0.33, player 2 win 0.67
Epoch 4, player 1 win 0.50, player 2 win 0.50
Epoch 5, player 1 win 0.40, player 2 win 0.60
Epoch 6, player 1 win 0.33, player 2 win 0.67
Epoch 7, player 1 win 0.43, player 2 win 0.57
Epoch 8, player 1 win 0.50, player 2 win 0.50
Epoch 9, player 1 win 0.56, player 2 win 0.44
Epoch 10, player 1 win 0.60, player 2 win 0.40
Epoch 11, player 1 win 0.64, player 2 win 0.36
Epoch 12, player 1 win 0.67, player 2 win 0.33
Epoch 13, player 1 win 0.69, player 2 win 0.31
Epoch 14, player 1 win 0.64, player 2 win 0.36
Epoch 15, player 1 win 0.67, player 2 win 0.33
Epoch 16, player 1 win 0.69, player 2 win 0.31
Epoch 17, player 1 win 0.71, player 2 win 0.29
Epoch 18, player 1 win 0.72, player 2 win 0.28
Epoch 19, player 1 win 0.74, player 2 win 0.26
Epoch 20, player 1 win 0.70, player 2 win 0.25
Epoch 21, player 1 win 0.71, player 2 win 0.24
Epoch 22, player 1 win

Epoch 318, player 1 win 0.29, player 2 win 0.07
Epoch 319, player 1 win 0.29, player 2 win 0.07
Epoch 320, player 1 win 0.29, player 2 win 0.07
Epoch 321, player 1 win 0.29, player 2 win 0.07
Epoch 322, player 1 win 0.29, player 2 win 0.07
Epoch 323, player 1 win 0.28, player 2 win 0.07
Epoch 324, player 1 win 0.28, player 2 win 0.07
Epoch 325, player 1 win 0.28, player 2 win 0.07
Epoch 326, player 1 win 0.28, player 2 win 0.07
Epoch 327, player 1 win 0.28, player 2 win 0.07
Epoch 328, player 1 win 0.28, player 2 win 0.07
Epoch 329, player 1 win 0.28, player 2 win 0.07
Epoch 330, player 1 win 0.28, player 2 win 0.07
Epoch 331, player 1 win 0.28, player 2 win 0.07
Epoch 332, player 1 win 0.28, player 2 win 0.07
Epoch 333, player 1 win 0.28, player 2 win 0.07
Epoch 334, player 1 win 0.28, player 2 win 0.07
Epoch 335, player 1 win 0.28, player 2 win 0.07
Epoch 336, player 1 win 0.28, player 2 win 0.07
Epoch 337, player 1 win 0.28, player 2 win 0.07
Epoch 338, player 1 win 0.28, player 2 w

Epoch 604, player 1 win 0.17, player 2 win 0.05
Epoch 605, player 1 win 0.17, player 2 win 0.05
Epoch 606, player 1 win 0.17, player 2 win 0.05
Epoch 607, player 1 win 0.17, player 2 win 0.05
Epoch 608, player 1 win 0.17, player 2 win 0.05
Epoch 609, player 1 win 0.17, player 2 win 0.05
Epoch 610, player 1 win 0.17, player 2 win 0.05
Epoch 611, player 1 win 0.17, player 2 win 0.05
Epoch 612, player 1 win 0.17, player 2 win 0.05
Epoch 613, player 1 win 0.17, player 2 win 0.05
Epoch 614, player 1 win 0.17, player 2 win 0.05
Epoch 615, player 1 win 0.17, player 2 win 0.05
Epoch 616, player 1 win 0.17, player 2 win 0.05
Epoch 617, player 1 win 0.17, player 2 win 0.05
Epoch 618, player 1 win 0.17, player 2 win 0.05
Epoch 619, player 1 win 0.17, player 2 win 0.05
Epoch 620, player 1 win 0.17, player 2 win 0.05
Epoch 621, player 1 win 0.17, player 2 win 0.05
Epoch 622, player 1 win 0.17, player 2 win 0.05
Epoch 623, player 1 win 0.17, player 2 win 0.04
Epoch 624, player 1 win 0.17, player 2 w

Epoch 916, player 1 win 0.20, player 2 win 0.07
Epoch 917, player 1 win 0.20, player 2 win 0.07
Epoch 918, player 1 win 0.20, player 2 win 0.07
Epoch 919, player 1 win 0.20, player 2 win 0.07
Epoch 920, player 1 win 0.20, player 2 win 0.07
Epoch 921, player 1 win 0.20, player 2 win 0.07
Epoch 922, player 1 win 0.20, player 2 win 0.07
Epoch 923, player 1 win 0.20, player 2 win 0.07
Epoch 924, player 1 win 0.19, player 2 win 0.07
Epoch 925, player 1 win 0.19, player 2 win 0.07
Epoch 926, player 1 win 0.19, player 2 win 0.07
Epoch 927, player 1 win 0.19, player 2 win 0.07
Epoch 928, player 1 win 0.19, player 2 win 0.07
Epoch 929, player 1 win 0.19, player 2 win 0.07
Epoch 930, player 1 win 0.19, player 2 win 0.07
Epoch 931, player 1 win 0.19, player 2 win 0.07
Epoch 932, player 1 win 0.19, player 2 win 0.07
Epoch 933, player 1 win 0.19, player 2 win 0.07
Epoch 934, player 1 win 0.19, player 2 win 0.07
Epoch 935, player 1 win 0.19, player 2 win 0.07
Epoch 936, player 1 win 0.19, player 2 w

Epoch 1172, player 1 win 0.16, player 2 win 0.06
Epoch 1173, player 1 win 0.16, player 2 win 0.06
Epoch 1174, player 1 win 0.16, player 2 win 0.06
Epoch 1175, player 1 win 0.16, player 2 win 0.06
Epoch 1176, player 1 win 0.16, player 2 win 0.06
Epoch 1177, player 1 win 0.16, player 2 win 0.06
Epoch 1178, player 1 win 0.16, player 2 win 0.06
Epoch 1179, player 1 win 0.16, player 2 win 0.06
Epoch 1180, player 1 win 0.16, player 2 win 0.06
Epoch 1181, player 1 win 0.16, player 2 win 0.06
Epoch 1182, player 1 win 0.16, player 2 win 0.06
Epoch 1183, player 1 win 0.16, player 2 win 0.06
Epoch 1184, player 1 win 0.16, player 2 win 0.06
Epoch 1185, player 1 win 0.16, player 2 win 0.06
Epoch 1186, player 1 win 0.16, player 2 win 0.06
Epoch 1187, player 1 win 0.16, player 2 win 0.06
Epoch 1188, player 1 win 0.16, player 2 win 0.06
Epoch 1189, player 1 win 0.16, player 2 win 0.06
Epoch 1190, player 1 win 0.16, player 2 win 0.06
Epoch 1191, player 1 win 0.16, player 2 win 0.06
Epoch 1192, player 1

...

Epoch 98872, player 1 win 0.03, player 2 win 0.01
Epoch 98873, player 1 win 0.03, player 2 win 0.01
Epoch 98874, player 1 win 0.03, player 2 win 0.01
Epoch 98875, player 1 win 0.03, player 2 win 0.01
Epoch 98876, player 1 win 0.03, player 2 win 0.01
Epoch 98877, player 1 win 0.03, player 2 win 0.01
Epoch 98878, player 1 win 0.03, player 2 win 0.01
Epoch 98879, player 1 win 0.03, player 2 win 0.01
Epoch 98880, player 1 win 0.03, player 2 win 0.01
Epoch 98881, player 1 win 0.03, player 2 win 0.01
Epoch 98882, player 1 win 0.03, player 2 win 0.01
Epoch 98883, player 1 win 0.03, player 2 win 0.01
Epoch 98884, player 1 win 0.03, player 2 win 0.01
Epoch 98885, player 1 win 0.03, player 2 win 0.01
Epoch 98886, player 1 win 0.03, player 2 win 0.01
Epoch 98887, player 1 win 0.03, player 2 win 0.01
Epoch 98888, player 1 win 0.03, player 2 win 0.01
Epoch 98889, player 1 win 0.03, player 2 win 0.01
Epoch 98890, player 1 win 0.03, player 2 win 0.01
Epoch 98891, player 1 win 0.03, player 2 win 0.01


Epoch 99146, player 1 win 0.03, player 2 win 0.01
Epoch 99147, player 1 win 0.03, player 2 win 0.01
Epoch 99148, player 1 win 0.03, player 2 win 0.01
Epoch 99149, player 1 win 0.03, player 2 win 0.01
Epoch 99150, player 1 win 0.03, player 2 win 0.01
Epoch 99151, player 1 win 0.03, player 2 win 0.01
Epoch 99152, player 1 win 0.03, player 2 win 0.01
Epoch 99153, player 1 win 0.03, player 2 win 0.01
Epoch 99154, player 1 win 0.03, player 2 win 0.01
Epoch 99155, player 1 win 0.03, player 2 win 0.01
Epoch 99156, player 1 win 0.03, player 2 win 0.01
Epoch 99157, player 1 win 0.03, player 2 win 0.01
Epoch 99158, player 1 win 0.03, player 2 win 0.01
Epoch 99159, player 1 win 0.03, player 2 win 0.01
Epoch 99160, player 1 win 0.03, player 2 win 0.01
Epoch 99161, player 1 win 0.03, player 2 win 0.01
Epoch 99162, player 1 win 0.03, player 2 win 0.01
Epoch 99163, player 1 win 0.03, player 2 win 0.01
Epoch 99164, player 1 win 0.03, player 2 win 0.01
Epoch 99165, player 1 win 0.03, player 2 win 0.01


Epoch 99437, player 1 win 0.03, player 2 win 0.01
Epoch 99438, player 1 win 0.03, player 2 win 0.01
Epoch 99439, player 1 win 0.03, player 2 win 0.01
Epoch 99440, player 1 win 0.03, player 2 win 0.01
Epoch 99441, player 1 win 0.03, player 2 win 0.01
Epoch 99442, player 1 win 0.03, player 2 win 0.01
Epoch 99443, player 1 win 0.03, player 2 win 0.01
Epoch 99444, player 1 win 0.03, player 2 win 0.01
Epoch 99445, player 1 win 0.03, player 2 win 0.01
Epoch 99446, player 1 win 0.03, player 2 win 0.01
Epoch 99447, player 1 win 0.03, player 2 win 0.01
Epoch 99448, player 1 win 0.03, player 2 win 0.01
Epoch 99449, player 1 win 0.03, player 2 win 0.01
Epoch 99450, player 1 win 0.03, player 2 win 0.01
Epoch 99451, player 1 win 0.03, player 2 win 0.01
Epoch 99452, player 1 win 0.03, player 2 win 0.01
Epoch 99453, player 1 win 0.03, player 2 win 0.01
Epoch 99454, player 1 win 0.03, player 2 win 0.01
Epoch 99455, player 1 win 0.03, player 2 win 0.01
Epoch 99456, player 1 win 0.03, player 2 win 0.01


Epoch 99710, player 1 win 0.03, player 2 win 0.01
Epoch 99711, player 1 win 0.03, player 2 win 0.01
Epoch 99712, player 1 win 0.03, player 2 win 0.01
Epoch 99713, player 1 win 0.03, player 2 win 0.01
Epoch 99714, player 1 win 0.03, player 2 win 0.01
Epoch 99715, player 1 win 0.03, player 2 win 0.01
Epoch 99716, player 1 win 0.03, player 2 win 0.01
Epoch 99717, player 1 win 0.03, player 2 win 0.01
Epoch 99718, player 1 win 0.03, player 2 win 0.01
Epoch 99719, player 1 win 0.03, player 2 win 0.01
Epoch 99720, player 1 win 0.03, player 2 win 0.01
Epoch 99721, player 1 win 0.03, player 2 win 0.01
Epoch 99722, player 1 win 0.03, player 2 win 0.01
Epoch 99723, player 1 win 0.03, player 2 win 0.01
Epoch 99724, player 1 win 0.03, player 2 win 0.01
Epoch 99725, player 1 win 0.03, player 2 win 0.01
Epoch 99726, player 1 win 0.03, player 2 win 0.01
Epoch 99727, player 1 win 0.03, player 2 win 0.01
Epoch 99728, player 1 win 0.03, player 2 win 0.01
Epoch 99729, player 1 win 0.03, player 2 win 0.01


Epoch 99980, player 1 win 0.03, player 2 win 0.01
Epoch 99981, player 1 win 0.03, player 2 win 0.01
Epoch 99982, player 1 win 0.03, player 2 win 0.01
Epoch 99983, player 1 win 0.03, player 2 win 0.01
Epoch 99984, player 1 win 0.03, player 2 win 0.01
Epoch 99985, player 1 win 0.03, player 2 win 0.01
Epoch 99986, player 1 win 0.03, player 2 win 0.01
Epoch 99987, player 1 win 0.03, player 2 win 0.01
Epoch 99988, player 1 win 0.03, player 2 win 0.01
Epoch 99989, player 1 win 0.03, player 2 win 0.01
Epoch 99990, player 1 win 0.03, player 2 win 0.01
Epoch 99991, player 1 win 0.03, player 2 win 0.01
Epoch 99992, player 1 win 0.03, player 2 win 0.01
Epoch 99993, player 1 win 0.03, player 2 win 0.01
Epoch 99994, player 1 win 0.03, player 2 win 0.01
Epoch 99995, player 1 win 0.03, player 2 win 0.01
Epoch 99996, player 1 win 0.03, player 2 win 0.01
Epoch 99997, player 1 win 0.03, player 2 win 0.01
Epoch 99998, player 1 win 0.03, player 2 win 0.01
Epoch 99999, player 1 win 0.03, player 2 win 0.01
